In [130]:
import pandas as pd


# Then load your CSV
df = pd.read_csv('Food_Inspections_20250414.csv')
df.head()

Inspection ID                                      DBA Name  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN/FIREHOUSE GRILL   
1        2608378                                   Babas Halal   
2        2614750                           CHICK-FIL-A PULLMAN   
3        2609909                                  HAPPY MARKET   
4        2609927                    SAT KAIVAL FOOD INC/SUBWAY   

                                       AKA Name  License #  Facility Type  \
0  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0     Restaurant   
1                                   Babas Halal  2684170.0     Restaurant   
2                           CHICK-FIL-A PULLMAN  3015728.0     Restaurant   
3                                  HAPPY MARKET  2912802.0  Grocery Store   
4                    SAT KAIVAL FOOD INC/SUBWAY  2728400.0     Restaurant   

              Risk               Address     City State      Zip  \
0    Risk 1 (High)      5648 W ROOSEVELT  CHICAGO    IL  60644.0   
1    Risk 1 (High)      7901 S DAMEN AVE  CHICAGO    IL  60620.0   
2    Risk 1 (High)   11131 S CORLISS AVE  CHICAGO    IL  60628.0   
3  Risk 2 (Medium)  2334 S WENTWORTH AVE  CHICAGO    IL  60616.0   
4    Risk 1 (High)       1916 S STATE ST  CHICAGO    IL  60616.0   

  Inspection Date Inspection Type             Results  \
0      06/18/2012       Complaint  Pass w/ Conditions   
1      12/03/2024       Complaint                Fail   
2      03/31/2025         License                Pass   
3      01/02/2025         Canvass  Pass w/ Conditions   
4      01/02/2025         Canvass                Pass   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [131]:
possible_missing_values = [
    'null', 'none', 'n/a', 'na', 'nan', 'missing', '0',"Unknown",
    '', ' ', '-', '--', 'n\\a', 'n.a.', 'n.a', 'na.', 'null.', 'none.',
    'no data', 'not available', 'not applicable', 'unavailable', 'tbd',
    'to be determined', 'nil', 'undefined', 'blank', 'empty', '?', "nulls"
]

def is_any_missing(val):
    if pd.isna(val):
        return True
    if isinstance(val, str):
        return val.strip().lower() in possible_missing_values
    return False

missing_mask = df.applymap(is_any_missing)
missing_summary = missing_mask.sum()

# Show result
if (missing_summary > 0).any():
    print("⚠️ Columns with missing-like values:")
    print(missing_summary[missing_summary > 0])
else:
    print("✅ LOOKS GOOD — No missing, null, unknown, or blank values found.")

/var/folders/7j/8d273yqs2dd7r7524ztn9cvm0000gn/T/ipykernel_47680/3468946236.py:15: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  missing_mask = df.applymap(is_any_missing)


⚠️ Columns with missing-like values:
DBA Name              78
AKA Name            2437
License #             18
Facility Type       5203
Risk                  82
Address                3
City                 159
State                 58
Zip                   39
Inspection Type        1
Violations         80432
Latitude             991
Longitude            991
Location             991
dtype: int64


In [110]:

# 1. Remove "DBA Name" and "Location" columns
df.drop(columns=['DBA Name', 'Location'], inplace=True, errors='ignore')

In [111]:

# 2. Convert ZIP column (e.g., 60644.0 → 60644 as string)
df['Zip'] = df['Zip'].apply(lambda x: str(int(x)) if pd.notnull(x) else 'Unknown')


In [112]:

# 3. Fill missing values
df['AKA Name'] = df['AKA Name'].fillna('Unknown')
df['License #'] = df['License #'].fillna('-1')
df['Facility Type'] = df['Facility Type'].fillna('Unknown')
df['Risk'] = df['Risk'].fillna('Unknown')
df['City'] = df['City'].fillna('Unknown')

In [113]:

# 4. Filter only rows where State is "IL"
df = df[df['State'] == 'IL']


In [114]:


# 5. Normalize values in "Inspection Type"
df['Inspection Type'] = df['Inspection Type'].fillna('Unknown')
df['Inspection Type'] = df['Inspection Type'].apply(
    lambda x: 'Follow-Up' if 're-' in x.lower() else
              'Complaint' if 'complaint' in x.lower() else
              'Routine' if x != 'Unknown' else 'Unknown'
)

In [115]:

# 6. Normalize values in "Results"
df['Results'] = df['Results'].replace({'No Entry': 'Unknown', 'Not Ready': 'Unknown', 'Out of Business': 'Unknown'})


In [116]:

# 7. Rename "AKA Name" to "Facility Name"
df.rename(columns={'AKA Name': 'Facility Name'}, inplace=True)


In [117]:
# 8. Combine Address + City + State into new Address format
df['Address'] = df['Address'].fillna('Unknown') + ', ' + df['City'] + ', IL'

In [118]:
df.rename(columns={'Zip': 'Zip Code'}, inplace=True)

In [119]:
df.head(10)

Inspection ID                                 Facility Name  License #  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
1        2608378                                   Babas Halal  2684170.0   
2        2614750                           CHICK-FIL-A PULLMAN  3015728.0   
3        2609909                                  HAPPY MARKET  2912802.0   
4        2609927                    SAT KAIVAL FOOD INC/SUBWAY  2728400.0   
5        1098818                             HAUGAN ELEMENTARY    23591.0   
6        1214298                                JOHNNY ROCKETS  2048281.0   
7        2610482                                        DANCEN  2341747.0   
8        2610081                  MARYS FOOD AND GROCERY STORE  2326530.0   
9        2610172                                          KOTO  2872350.0   

   Facility Type             Risk                            Address     City  \
0     Restaurant    Risk 1 (High)      5648 W ROOSEVELT, CHICAGO, IL  CHICAGO   
1     Restaurant    Risk 1 (High)      7901 S DAMEN AVE, CHICAGO, IL  CHICAGO   
2     Restaurant    Risk 1 (High)   11131 S CORLISS AVE, CHICAGO, IL  CHICAGO   
3  Grocery Store  Risk 2 (Medium)  2334 S WENTWORTH AVE, CHICAGO, IL  CHICAGO   
4     Restaurant    Risk 1 (High)       1916 S STATE ST, CHICAGO, IL  CHICAGO   
5         School    Risk 1 (High)     4540 N Hamlin AVE, CHICAGO, IL  CHICAGO   
6     Restaurant    Risk 1 (High)        177 N State ST, CHICAGO, IL  CHICAGO   
7     Restaurant    Risk 1 (High)    5114 N LINCOLN AVE, CHICAGO, IL  CHICAGO   
8     Restaurant    Risk 1 (High)  1901 S CANALPORT AVE, CHICAGO, IL  CHICAGO   
9     Restaurant    Risk 1 (High)         258 W 31ST ST, CHICAGO, IL  CHICAGO   

  State Zip Code Inspection Date Inspection Type             Results  \
0    IL    60644      06/18/2012       Complaint  Pass w/ Conditions   
1    IL    60620      12/03/2024       Complaint                Fail   
2    IL    60628      03/31/2025         Routine                Pass   
3    IL    60616      01/02/2025         Routine  Pass w/ Conditions   
4    IL    60616      01/02/2025         Routine                Pass   
5    IL    60625      01/31/2013         Routine                Pass   
6    IL    60601      03/07/2012       Follow-Up                Pass   
7    IL    60625      01/14/2025         Routine             Unknown   
8    IL    60616      01/06/2025         Routine                Pass   
9    IL    60616      01/07/2025         Routine                Pass   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              

In [120]:
import pandas as pd
import re

# Assuming df is your full original DataFrame with a column named 'Violations'

def parse_violations_row(row):
    # Extract the original columns (excluding 'Violations')
    original_data = row.drop(labels=['Violations']).to_dict()
    
    violations_text = row['Violations']
    if pd.isna(violations_text):
        return []

    chunks = re.split(r'(?=\d{2}\. )', violations_text)  # Split on each violation start
    rows = []
    for chunk in chunks:
        match = re.match(r'(?P<violation_code>\d+)\.\s[*]?\s?(?P<violation_description>.+?)\s+-\s+Comments:\s*(?P<violation_comment>.+)', chunk.strip(), re.DOTALL)
        if match:
            violation = match.groupdict()
            violation.update(original_data)  # Add original row metadata
            rows.append(violation)
    return rows

# Flatten all rows with original data included
all_violations = []
for _, row in df.iterrows():
    all_violations.extend(parse_violations_row(row))

# Create the final DataFrame
df = pd.DataFrame(all_violations)

# Preview the result
df.head(20)

violation_code  \
0              21   
1              32   
2              33   
3              34   
4              35   
5              36   
6              40   
7               1   
8              10   
9              10   
10             10   
11             10   
12             21   
13             22   
14             39   
15             41   
16             47   
17             47   
18             49   
19             51   

                                                                                                   violation_description  \
0                               CERTIFIED FOOD MANAGER ON SITE WHEN POTENTIALLY HAZARDOUS FOODS ARE  PREPARED AND SERVED   
1                                       FOOD AND NON-FOOD CONTACT SURFACES PROPERLY DESIGNED, CONSTRUCTED AND MAINTAINED   
2                                        FOOD AND NON-FOOD CONTACT EQUIPMENT UTENSILS CLEAN, FREE OF ABRASIVE DETERGENTS   
3                  FLOORS: CONSTRUCTED PER CODE, CLEANED, GOOD REPAIR, COVING INSTALLED, DUST-LESS CLEANING METHODS USED   
4   WALLS, CEILINGS, ATTACHED EQUIPMENT CONSTRUCTED PER CODE: GOOD REPAIR, SURFACES CLEAN AND DUST-LESS CLEANING METHODS   
5                                           LIGHTING: REQUIRED MINIMUM FOOT-CANDLES OF LIGHT PROVIDED, FIXTURES SHIELDED   
6                                                     REFRIGERATION AND METAL STEM THERMOMETERS PROVIDED AND CONSPICUOUS   
7                                                  PERSON IN CHARGE PRESENT, DEMONSTRATES KNOWLEDGE, AND PERFORMS DUTIES   
8                                                            ADEQUATE HANDWASHING SINKS PROPERLY SUPPLIED AND ACCESSIBLE   
9                                                            ADEQUATE HANDWASHING SINKS PROPERLY SUPPLIED AND ACCESSIBLE   
10                                                           ADEQUATE HANDWASHING SINKS PROPERLY SUPPLIED AND ACCESSIBLE   
11                                                           ADEQUATE HANDWASHING SINKS PROPERLY SUPPLIED AND ACCESSIBLE   
12                                                                                       PROPER HOT HOLDING TEMPERATURES   
13                                                                                      PROPER COLD HOLDING TEMPERATURES   
14                                                    CONTAMINATION PREVENTED DURING FOOD PREPARATION, STORAGE & DISPLAY   
15                                                                                 WIPING CLOTHS: PROPERLY USED & STORED   
16                                     FOOD & NON-FOOD CONTACT SURFACES CLEANABLE, PROPERLY DESIGNED, CONSTRUCTED & USED   
17                                     FOOD & NON-FOOD CONTACT SURFACES CLEANABLE, PROPERLY DESIGNED, CONSTRUCTED & USED   
18                                                                                  NON-FOOD/FOOD CONTACT SURFACES CLEAN   
19                                                                           PLUMBING INSTALLED; PROPER BACKFLOW DEVICES   

                                                                                                                                                                                                                                                                                                                                                                                                                                                            violation_comment  \
0                                                                                                                                                                                                                                                                                         OBSERVED NO CERTIFIED FOOD MANAGER ON DUTY WHILE (CHICKEN,FISH,FRENCH FRIES,ETC)IS BEING PREPARED ,SERVED & HANDLED AT THIS TIME.MUST BE ON SITE AT ALL TIMES.(SERIOUS 7-38-012). |   
1                         

In [121]:
df = df.rename(columns={
    'violation_code': 'Violation Code',
    'violation_description': 'Violation Description',
    'violation_comment': 'Violation Comment'
})


In [122]:
df.head()

Violation Code  \
0             21   
1             32   
2             33   
3             34   
4             35   

                                                                                                  Violation Description  \
0                              CERTIFIED FOOD MANAGER ON SITE WHEN POTENTIALLY HAZARDOUS FOODS ARE  PREPARED AND SERVED   
1                                      FOOD AND NON-FOOD CONTACT SURFACES PROPERLY DESIGNED, CONSTRUCTED AND MAINTAINED   
2                                       FOOD AND NON-FOOD CONTACT EQUIPMENT UTENSILS CLEAN, FREE OF ABRASIVE DETERGENTS   
3                 FLOORS: CONSTRUCTED PER CODE, CLEANED, GOOD REPAIR, COVING INSTALLED, DUST-LESS CLEANING METHODS USED   
4  WALLS, CEILINGS, ATTACHED EQUIPMENT CONSTRUCTED PER CODE: GOOD REPAIR, SURFACES CLEAN AND DUST-LESS CLEANING METHODS   

                                                                                                                                                                                                                          Violation Comment  \
0                                                       OBSERVED NO CERTIFIED FOOD MANAGER ON DUTY WHILE (CHICKEN,FISH,FRENCH FRIES,ETC)IS BEING PREPARED ,SERVED & HANDLED AT THIS TIME.MUST BE ON SITE AT ALL TIMES.(SERIOUS 7-38-012). |   
1                                              MUST PROVIDE SINK STOPPERS FOR 3- COMPARTMENT SINK.MUST REPAIR OR REPLACE WORN GASKETS ON REACH IN FREEZERS.MUST REMOVE RUST FROM LOWER SHELF OF PREP TABLE,WALK IN COOLER SHELVING UNITS. |   
2  MUST CLEAN GREASE & FOOD DEBRI FROM SHELVING UNITS IN PREP COOLER,FILTERS AT HOOD,ROLLING CART,PREP TABLE,DEEP FRYER,WINDOW SILLS,POP SLEEVES,LIGHT SHIELDS,PIPES OF COOKING EQUIPMENT,FAN GUARDS IN WALK IN COOLER,VENTILATION VENTS. |   
3                                                                                                                                                                                      MUST CLEAN FLOOR IN WALK IN COOLER & FLOOR DRAINS. |   
4                                                                                                                                   MUST REPAIR OR REPLACE MISSING WALL BASES UNDER FRONT HAND SINK & STAINED CEILING TILES IN REAR AREA. |   

   Inspection ID                                 Facility Name  License #  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
1        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
2        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
3        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
4        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   

  Facility Type           Risk                        Address     City State  \
0    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
1    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
2    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
3    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
4    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   

  Zip Code Inspection Date Inspection Type             Results   Latitude  \
0    60644      06/18/2012       Complaint  Pass w/ Conditions  41.865679   
1    60644      06/18/2012       Complaint  Pass w/ Conditions  41.865679   
2    60644      06/18/2012       Complaint  Pass w/ Conditions  41.865679   
3    60644      06/18/2012       Complaint  Pass w/ Conditions  41.865679   
4    60644      06/18/2012       Complaint  Pass w/ Conditions  41.865679   

   Longitude  
0 -87.766331  
1 -87.766331  
2 -87.766331  
3 -87.766331  
4 -87.766331

In [123]:
df['Latitude'] = df['Latitude'].round(5)
df['Longitude'] = df['Longitude'].round(5)


In [124]:
df.head()

Violation Code  \
0             21   
1             32   
2             33   
3             34   
4             35   

                                                                                                  Violation Description  \
0                              CERTIFIED FOOD MANAGER ON SITE WHEN POTENTIALLY HAZARDOUS FOODS ARE  PREPARED AND SERVED   
1                                      FOOD AND NON-FOOD CONTACT SURFACES PROPERLY DESIGNED, CONSTRUCTED AND MAINTAINED   
2                                       FOOD AND NON-FOOD CONTACT EQUIPMENT UTENSILS CLEAN, FREE OF ABRASIVE DETERGENTS   
3                 FLOORS: CONSTRUCTED PER CODE, CLEANED, GOOD REPAIR, COVING INSTALLED, DUST-LESS CLEANING METHODS USED   
4  WALLS, CEILINGS, ATTACHED EQUIPMENT CONSTRUCTED PER CODE: GOOD REPAIR, SURFACES CLEAN AND DUST-LESS CLEANING METHODS   

                                                                                                                                                                                                                          Violation Comment  \
0                                                       OBSERVED NO CERTIFIED FOOD MANAGER ON DUTY WHILE (CHICKEN,FISH,FRENCH FRIES,ETC)IS BEING PREPARED ,SERVED & HANDLED AT THIS TIME.MUST BE ON SITE AT ALL TIMES.(SERIOUS 7-38-012). |   
1                                              MUST PROVIDE SINK STOPPERS FOR 3- COMPARTMENT SINK.MUST REPAIR OR REPLACE WORN GASKETS ON REACH IN FREEZERS.MUST REMOVE RUST FROM LOWER SHELF OF PREP TABLE,WALK IN COOLER SHELVING UNITS. |   
2  MUST CLEAN GREASE & FOOD DEBRI FROM SHELVING UNITS IN PREP COOLER,FILTERS AT HOOD,ROLLING CART,PREP TABLE,DEEP FRYER,WINDOW SILLS,POP SLEEVES,LIGHT SHIELDS,PIPES OF COOKING EQUIPMENT,FAN GUARDS IN WALK IN COOLER,VENTILATION VENTS. |   
3                                                                                                                                                                                      MUST CLEAN FLOOR IN WALK IN COOLER & FLOOR DRAINS. |   
4                                                                                                                                   MUST REPAIR OR REPLACE MISSING WALL BASES UNDER FRONT HAND SINK & STAINED CEILING TILES IN REAR AREA. |   

   Inspection ID                                 Facility Name  License #  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
1        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
2        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
3        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
4        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   

  Facility Type           Risk                        Address     City State  \
0    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
1    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
2    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
3    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   
4    Restaurant  Risk 1 (High)  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL   

  Zip Code Inspection Date Inspection Type             Results  Latitude  \
0    60644      06/18/2012       Complaint  Pass w/ Conditions  41.86568   
1    60644      06/18/2012       Complaint  Pass w/ Conditions  41.86568   
2    60644      06/18/2012       Complaint  Pass w/ Conditions  41.86568   
3    60644      06/18/2012       Complaint  Pass w/ Conditions  41.86568   
4    60644      06/18/2012       Complaint  Pass w/ Conditions  41.86568   

   Longitude  
0  -87.76633  
1  -87.76633  
2  -87.76633  
3  -87.76633  
4  -87.76633

In [125]:
df = df.drop(columns=['City', 'State'], errors='ignore')


In [126]:
df['Latitude'] = df['Latitude'].fillna(-1)
df['Longitude'] = df['Longitude'].fillna(-1)


In [127]:
# Count of missing values before fill
print("Missing Latitude:", df['Latitude'].isna().sum())
print("Missing Longitude:", df['Longitude'].isna().sum())

Missing Latitude: 0
Missing Longitude: 0


In [128]:
possible_missing_values = [
    'null', 'none', 'n/a', 'na', 'nan', 'missing', '0',"Unknown",
    '', ' ', '-', '--', 'n\\a', 'n.a.', 'n.a', 'na.', 'null.', 'none.',
    'no data', 'not available', 'not applicable', 'unavailable', 'tbd',
    'to be determined', 'nil', 'undefined', 'blank', 'empty', '?', "nulls"
]

def is_any_missing(val):
    if pd.isna(val):
        return True
    if isinstance(val, str):
        return val.strip().lower() in possible_missing_values
    return False

missing_mask = df.applymap(is_any_missing)
missing_summary = missing_mask.sum()

# Show result
if (missing_summary > 0).any():
    print("⚠️ Columns with missing-like values:")
    print(missing_summary[missing_summary > 0])
else:
    print("✅ LOOKS GOOD — No missing, null, unknown, or blank values found.")

/var/folders/7j/8d273yqs2dd7r7524ztn9cvm0000gn/T/ipykernel_47680/3468946236.py:15: FutureWarning: DataFrame.applymap has been deprecated. Use DataFrame.map instead.
  missing_mask = df.applymap(is_any_missing)


⚠️ Columns with missing-like values:
Facility Name    13
dtype: int64


In [129]:
df[df['License #'] == 0]

Violation Code  \
1731               55   
1865                3   
1866               10   
1867               10   
1868               38   
1869               55   
1870               55   
1871               56   
7669               35   
7670               40   
7671               49   
7672               51   
7673               52   
7674               53   
7675               55   
7676               55   
7677               55   
7678               57   
9234               33   
9235               39   
9236               55   
9237               64   
9770               33   
9771               39   
9772               55   
9773               64   
9793               51   
9794               55   
9795               55   
12956               2   
12957              49   
15312              38   
16656              51   
17652               5   
17653              38   
17654              38   
17655              38   
17656              49   
17657              50   
17658              54   
17659              55   
17660              55   
18267              16   
18268              39   
18269              49   
18270              51   
18271              51   
18272              55   
19870              10   
19871              38   
19872              47   
19873              53   
19874              55   
21250               2   
21251              64   
21252              64   
25106              10   
25107              38   
25108              38   
25109              40   
25110              45   
25111              49   
25112              54   
25113              55   
25114              55   
25115              55   
25742               1   
25743              10   
25744              36   
25745              36   
25746              38   
25747              38   
25748              47   
25749              47   
25750              48   
25751              48   
25752              51   
25753              51   
25754              53   
25755              53   
25756              54   
25757              55   
25758              55   
25759              55   
25760              56   
29523               3   
29524              37   
29525              38   
29526              38   
29527              44   
29528              45   
29529              47   
29530              47   
29531              49   
29532              54   
29533              55   
29534              55   
29535              55   
29536              55   
29537              55   
29538              57   
50067               2   
50068              10   
50069              10   
50070              21   
50071              23   
50072              36   
50073              38   
50074              38   
50075              47   
50076              48   
50077              49   
50078              50   
50079              55   
50080              57   
50081              58   
52091               3   
52092              10   
52093              10   
52094              28   
52095              38   
52096              48   
52097              53   
52098              54   
52099              57   
52677               2   
52678              10   
52679              10   
52680              47   
52681              47   
52682              49   
52683              55   
52684              55   
52685              57   
52944              56   
60143               3   
60144              22   
60145              28   
60146              36   
60147              37   
60148              38   
60149              38   
60150              44   
60151              45   
60152              47   
60153              47   
60154              48   
60155              49   
60156              53   
60157              54   
60158              55   
60159              55   
60160              55   
60161              55   
60162              55   
60163              57   
61475               1   
61476              10   
61477              10   
61478  

In [100]:
# Replace float 0.0 with -1 in 'License #'
df['License #'] = df['License #'].apply(lambda x: -1 if x == 0.0 else x)


In [ ]:
df[df['License #'] == 0]

In [103]:
df['Risk'] = df['Risk'].str.extract(r'\((.*?)\)')

In [104]:
df.head()

Violation Code  \
0             21   
1             32   
2             33   
3             34   
4             35   

                                                                                                  Violation Description  \
0                              CERTIFIED FOOD MANAGER ON SITE WHEN POTENTIALLY HAZARDOUS FOODS ARE  PREPARED AND SERVED   
1                                      FOOD AND NON-FOOD CONTACT SURFACES PROPERLY DESIGNED, CONSTRUCTED AND MAINTAINED   
2                                       FOOD AND NON-FOOD CONTACT EQUIPMENT UTENSILS CLEAN, FREE OF ABRASIVE DETERGENTS   
3                 FLOORS: CONSTRUCTED PER CODE, CLEANED, GOOD REPAIR, COVING INSTALLED, DUST-LESS CLEANING METHODS USED   
4  WALLS, CEILINGS, ATTACHED EQUIPMENT CONSTRUCTED PER CODE: GOOD REPAIR, SURFACES CLEAN AND DUST-LESS CLEANING METHODS   

                                                                                                                                                                                                                          Violation Comment  \
0                                                       OBSERVED NO CERTIFIED FOOD MANAGER ON DUTY WHILE (CHICKEN,FISH,FRENCH FRIES,ETC)IS BEING PREPARED ,SERVED & HANDLED AT THIS TIME.MUST BE ON SITE AT ALL TIMES.(SERIOUS 7-38-012). |   
1                                              MUST PROVIDE SINK STOPPERS FOR 3- COMPARTMENT SINK.MUST REPAIR OR REPLACE WORN GASKETS ON REACH IN FREEZERS.MUST REMOVE RUST FROM LOWER SHELF OF PREP TABLE,WALK IN COOLER SHELVING UNITS. |   
2  MUST CLEAN GREASE & FOOD DEBRI FROM SHELVING UNITS IN PREP COOLER,FILTERS AT HOOD,ROLLING CART,PREP TABLE,DEEP FRYER,WINDOW SILLS,POP SLEEVES,LIGHT SHIELDS,PIPES OF COOKING EQUIPMENT,FAN GUARDS IN WALK IN COOLER,VENTILATION VENTS. |   
3                                                                                                                                                                                      MUST CLEAN FLOOR IN WALK IN COOLER & FLOOR DRAINS. |   
4                                                                                                                                   MUST REPAIR OR REPLACE MISSING WALL BASES UNDER FRONT HAND SINK & STAINED CEILING TILES IN REAR AREA. |   

   Inspection ID                                 Facility Name  License #  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
1        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
2        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
3        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   
4        1170324  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0   

  Facility Type  Risk                        Address     City State Zip Code  \
0    Restaurant  High  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL    60644   
1    Restaurant  High  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL    60644   
2    Restaurant  High  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL    60644   
3    Restaurant  High  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL    60644   
4    Restaurant  High  5648 W ROOSEVELT, CHICAGO, IL  CHICAGO    IL    60644   

  Inspection Date Inspection Type             Results  Latitude  Longitude  
0      06/18/2012       Complaint  Pass w/ Conditions  41.86568  -87.76633  
1      06/18/2012       Complaint  Pass w/ Conditions  41.86568  -87.76633  
2      06/18/2012       Complaint  Pass w/ Conditions  41.86568  -87.76633  
3      06/18/2012       Complaint  Pass w/ Conditions  41.86568  -87.76633  
4      06/18/2012       Complaint  Pass w/ Conditions  41.86568  -87.76633

In [105]:
# Normalize and check for missing-like values
normalized_risk = df['Risk'].astype(str).str.strip().str.lower()
mask = normalized_risk.isin(possible_missing_values)

# Display unique missing-like values
missing_risk_values = normalized_risk[mask].unique()
print("🧾 Unique missing-like values in 'Risk':")
print(missing_risk_values)


🧾 Unique missing-like values in 'Risk':
['nan']


In [106]:
df['Risk'] = df['Risk'].apply(lambda x: 'Unknown' if is_any_missing(x) else x)


In [107]:
# Normalize and check for missing-like values
normalized_risk = df['Risk'].astype(str).str.strip().str.lower()
mask = normalized_risk.isin(possible_missing_values)

# Display unique missing-like values
missing_risk_values = normalized_risk[mask].unique()
print("🧾 Unique missing-like values in 'Risk':")
print(missing_risk_values)


🧾 Unique missing-like values in 'Risk':
[]


In [132]:
df.head()

Inspection ID                                      DBA Name  \
0        1170324  CAPTAIN HOOKS FISH & CHICKEN/FIREHOUSE GRILL   
1        2608378                                   Babas Halal   
2        2614750                           CHICK-FIL-A PULLMAN   
3        2609909                                  HAPPY MARKET   
4        2609927                    SAT KAIVAL FOOD INC/SUBWAY   

                                       AKA Name  License #  Facility Type  \
0  CAPTAIN HOOKS FISH & CHICKEN FIREHOUSE GRILL  1804138.0     Restaurant   
1                                   Babas Halal  2684170.0     Restaurant   
2                           CHICK-FIL-A PULLMAN  3015728.0     Restaurant   
3                                  HAPPY MARKET  2912802.0  Grocery Store   
4                    SAT KAIVAL FOOD INC/SUBWAY  2728400.0     Restaurant   

              Risk               Address     City State      Zip  \
0    Risk 1 (High)      5648 W ROOSEVELT  CHICAGO    IL  60644.0   
1    Risk 1 (High)      7901 S DAMEN AVE  CHICAGO    IL  60620.0   
2    Risk 1 (High)   11131 S CORLISS AVE  CHICAGO    IL  60628.0   
3  Risk 2 (Medium)  2334 S WENTWORTH AVE  CHICAGO    IL  60616.0   
4    Risk 1 (High)       1916 S STATE ST  CHICAGO    IL  60616.0   

  Inspection Date Inspection Type             Results  \
0      06/18/2012       Complaint  Pass w/ Conditions   
1      12/03/2024       Complaint                Fail   
2      03/31/2025         License                Pass   
3      01/02/2025         Canvass  Pass w/ Conditions   
4      01/02/2025         Canvass                Pass   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       

In [108]:
df.to_csv('Chicago_cleaned3.csv', index=False)